# cronData - Versión 1.0.

In [ ]:
#!/usr/bin/python3
# -*- coding: utf-8 -*-


#################################################################################################### 100
#####  CRONDATA  ###################################################################################
 #
 #    18/03/27    Python 3.5.4.    cronData 1.0.
 #
#####  Juan de Dios Yáñez Ávila  ###  juandediosyanez@gmail.com  ###  www.onw4rds.com  #############
#################################################################################################### 100


from email import encoders
from email.message import Message
from email.mime.audio import MIMEAudio
from email.mime.base import MIMEBase
from email.mime.image import MIMEImage
from email.mime.multipart import MIMEMultipart
from email.mime.text import MIMEText

import datetime
import os
import smtplib
import socket
import subprocess
import time


time.sleep(20)
datos = {"dispositive": str(), "ip":str(), "elapsed_time":int(), "cpu_temperature":float()}
initial_time = datetime.datetime.now()


def send_email():
    global datos

    ## Definimos SMTP del email
    smtp_server = "stmp.gmail.com"
    smtp_user = "onw4rds@gmail.com"
    smtp_pass = "#GOovh47536485q??"
    
    ## Construimos el email
    message = MIMEMultipart('alternative')
    message['From'] = "onw4rds@gmail.com"
    message['To'] = "onw4rds@gmail.com"  
    message['Subject'] = str(datos["dispositive"])+" | "+str(datos["ip"])+" | CPU: "+str(datos["cpu_temperature"])+"ºC || cronData 1.0."
    text = "Conexión establecida a las {0} del dispositivo {1} en la dirección IP {2}".format(initial_time, datos["dispositive"], datos["ip"]) 
    part1 = MIMEText(text, 'plain')
    message.attach(part1)
    
    ## Adjuntamos archivo
    fp = open("/home/pi/data/cronData/cronData.txt", 'rb') # se ve la dirección desde index
    attached = MIMEBase('multipart', 'encrypted')
    attached.set_payload(fp.read())
    fp.close()
    
    ## Encriptamos archivo.
    encoders.encode_base64( attached )
    attached.add_header('Content-Disposition', 'attachment', filename = "cron01.txt")
    message.attach( attached )
    
    ## Script para el envío del correo electrónico a la dirección indicada
    mailServer = smtplib.SMTP('smtp.gmail.com', 587)
    mailServer.ehlo()
    mailServer.starttls()
    mailServer.ehlo()
    mailServer.login(smtp_user, smtp_pass)
    mailServer.sendmail("onw4rds@gmail.com", "onw4rds@gmail.com", message.as_string())
    mailServer.quit()


file_datos = open("/home/pi/data/cronData/cronData.txt", "w")
file_datos.close()

while(True):
    # Name and IP
    datos["dispositive"] = socket.gethostname()
    datos["ip"] = subprocess.getoutput('hostname -I')
    
    # Elapsed time since active
    current_time = datetime.datetime.now()
    elapsed_time = current_time - initial_time
    elapsed_time = int(elapsed_time.seconds/60)
    datos["elapsed_time"] = elapsed_time
    
    # Temperature of CPU
    tempFile = open( "/sys/class/thermal/thermal_zone0/temp" )
    cpu_temp = tempFile.read()
    tempFile.close()
    datos["cpu_temperature"] = float(cpu_temp)/1000
    
    # Save data
    file_datos = open("/home/pi/data/cronData/cronData.txt", "a")
    aux = str(datos["dispositive"])+" | "+str(datos["ip"])+" | "+str(datos["elapsed_time"])+" minutes | "+str(datos["cpu_temperature"])+" ºC |\n"
    file_datos.write(aux)
    file_datos.close()
    
    # Send data
    send_email()
    
    # Wait for the next minute to reboot and take information
    time.sleep(60)

# cronData - Versión 0.1.

In [ ]:
#!/usr/bin/python3
# -*- coding: utf-8 -*-

##### CRONDATA #####
 #
 #    18/03/27    Python 3.5.4.    cronData 0.1.
 #
 #    Juan de Dios Yáñez Ávila | juandediosyanez@gmail.com | www.onw4rds.com
 #
#####

from email import encoders
from email.message import Message
from email.mime.audio import MIMEAudio
from email.mime.base import MIMEBase
from email.mime.image import MIMEImage
from email.mime.multipart import MIMEMultipart
from email.mime.text import MIMEText

import datetime
import matplotlib.pyplot as plt
import numpy as np
import os
import smtplib
import socket
import subprocess
import time

#################################################################################################### 100

# Tenemos que dar un tiempo al sistema para que se establezca conexión a red y no de error.
# Ya que necesitamos conocer la IP de conexión y si no tenemos conexión a internet tampoco
# iniciará el programa.
time.sleep(30)

#################################################################################################### 100

# Obtención de datos
connection_time = datetime.datetime.now()       # fecha de establecimiento de conexión
dispositive = socket.gethostname()              # nombre del dispositivo
ip = subprocess.getoutput('hostname -I')        # IP del dispositivo
elapsed_time = 0                                # tiempo transcurrido de conexión

# Listas de datos
cpu_temp_list = list()
gpu_temp_list = list()
time_list = list()

#################################################################################################### 100

def get_cpu_temp():
    tempFile = open( "/sys/class/thermal/thermal_zone0/temp" )
    cpu_temp = tempFile.read()
    tempFile.close()
    cpu_temp = float(cpu_temp)/1000
    return cpu_temp

def get_gpu_temp():
    gpu_temp = subprocess.getoutput( "/opt/vc/bin/vcgencmd measure_temp" ).replace( 'temp=', '' ).replace( 'C', '' )
    gpu_temp = float(gpu_temp[:-1])
    return gpu_temp
    
#################################################################################################### 100

def make_graph(time_list, cpu_temp_list, gpu_temp_list):
    cpu_temp_arr = np.array(cpu_temp_list)
    gpu_temp_arr = np.array(gpu_temp_list)
    time_arr = np.array(time_list)
    
    fig, axes = plt.subplots()
    axes.plot(time_arr, cpu_temp_arr, label="CPU") # blue line with dots
    axes.plot(time_arr, gpu_temp_arr, label="GPU") # green dashed line
    axes.set_xlabel("TIME")
    axes.set_ylabel("TEMPERATURE")
    axes.set_title('TEMPERATURE OF DISPOSITIVE')
    plt.legend()   
    fig.savefig("/home/pi/data/cronData/cronData.jpg")
    
#################################################################################################### 100
    
def send_data(name_file, connection_time, dispositive, ip):
    global cpu_temp_list
    global gpu_temp_list
    global time_list
    
    addr_to = "onw4rds@gmail.com"
    addr_from = "onw4rds@gmail.com"
    ## Definimos SMTP del email
    smtp_server = "stmp.gmail.com"
    smtp_user = "onw4rds@gmail.com"
    smtp_pass = "#GOovh47536485q??"
    ## Construimos el email
    message = MIMEMultipart('alternative')
    message['From'] = addr_from
    message['To'] = addr_to  
    message['Subject'] = str(dispositive)+" | "+str(ip)+" | CPU: "+str(cpu_temp_list[-1])+"ºC | GPU: "+str(gpu_temp_list[-1])+"ºC || cronData 1.1."
    text = """
              Dispositivo:  {0}
              IP:    {1}
              Conexión establecida a las:  {2}
              Temperatura de la CPU: {3} ºC
              Temperatura de la GPU: {4} ºC
                       
              Tiempo de funcionamiento aproximado: {5} minutos""".format(dispositive, ip, 
                                                                         connection_time, 
                                                                         cpu_temp_list[-1], 
                                                                         gpu_temp_list[-1],
                                                                         time_list[-1])
    part1 = MIMEText(text, 'plain')
    message.attach(part1)
    
    fp = open(str(name_file), 'rb') # se ve la dirección desde index
    attached = MIMEBase('multipart', 'encrypted')
    attached.set_payload(fp.read())
    fp.close()
    # Encriptamos archivo.
    encoders.encode_base64( attached )
    attached.add_header('Content-Disposition', 'attachment', filename = "cronData.jpg")
    message.attach( attached )
    ## Script para el envío del correo electrónico a la dirección indicada
    mailServer = smtplib.SMTP('smtp.gmail.com', 587)
    mailServer.ehlo()
    mailServer.starttls()
    mailServer.ehlo()
    mailServer.login(smtp_user, smtp_pass)
    mailServer.sendmail(addr_from, addr_to, message.as_string())
    mailServer.quit()

#################################################################################################### 100
while(True):
    try:
        while(True):
            #
            ip = subprocess.getoutput('hostname -I')    # IP del dispositivo
            print(ip)
   
            time_list.append(elapsed_time)
            cpu_temp_list.append( get_cpu_temp() )
            gpu_temp_list.append( get_gpu_temp() )
            make_graph(time_list, cpu_temp_list, gpu_temp_list)
    
            send_data("/home/pi/data/cronData/cronData.jpg", connection_time, dispositive, ip)
    
            time.sleep(60)
            elapsed_time += 1
    except:
        print(sys.exc_info())
        pass
    
#################################################################################################### 100

192.168.1.107 
192.168.1.107 
192.168.1.107 
192.168.1.107 
192.168.1.107 


# cronData - Versión 1.1.

In [ ]:
#!/usr/bin/python
# -*- coding: utf-8 -*-

##### CRONDATA #####
 #
 #    18/03/27    Python 3.5.4.    cronData 0.0.1.
 #
 #    Juan de Dios Yáñez Ávila | juandediosyanez@gmail.com | www.onw4rds.com
 #
#####

from email import encoders
from email.message import Message
from email.mime.audio import MIMEAudio
from email.mime.base import MIMEBase
from email.mime.image import MIMEImage
from email.mime.multipart import MIMEMultipart
from email.mime.text import MIMEText

import datetime
import matplotlib.pyplot as plt
import numpy as np
import os
import smtplib
import socket
import subprocess
import time

#################################################################################################### 100

# Tenemos que dar un tiempo al sistema para que se establezca conexión a red y no de error.
# Ya que necesitamos conocer la IP de conexión y si no tenemos conexión a internet tampoco
# iniciará el programa.
time.sleep(30)

#################################################################################################### 100

# Obtención de datos
connection_time = datetime.datetime.now()       # fecha de establecimiento de conexión
dispositive = socket.gethostname()      # nombre del dispositivo
ip = subprocess.getoutput('hostname -I')    # IP del dispositivo
elapsed_time = 0                         # tiempo transcurrido de conexión

# Listas de datos
cpu_temp_list = list()
gpu_temp_list = list()
time_list = list()

#################################################################################################### 100

def get_cpu_temp():
    tempFile = open( "/sys/class/thermal/thermal_zone0/temp" )
    cpu_temp = tempFile.read()
    tempFile.close()
    cpu_temp = float(cpu_temp)/1000
    return cpu_temp

def get_gpu_temp():
    gpu_temp = subprocess.getoutput( "/opt/vc/bin/vcgencmd measure_temp" ).replace( 'temp=', '' ).replace( 'C', '' )
    gpu_temp = float(gpu_temp[:-1])
    return gpu_temp
    
#################################################################################################### 100

def make_graph(time_list, cpu_temp_list, gpu_temp_list):
    cpu_temp_arr = np.array(cpu_temp_list)
    gpu_temp_arr = np.array(gpu_temp_list)
    time_arr = np.array(time_list)
    
    fig, axes = plt.subplots()
    axes.plot(time_arr, cpu_temp_arr, label="CPU") # blue line with dots
    axes.plot(time_arr, gpu_temp_arr, label="GPU") # green dashed line
    axes.set_xlabel("TIME")
    axes.set_ylabel("TEMPERATURE")
    axes.set_title('TEMPERATURE OF DISPOSITIVE')
    plt.legend()   
    fig.savefig("cronData.png")
    
#################################################################################################### 100
    
def send_data(name_file, connection_time, dispositive, ip):
    global cpu_temp_list
    global gpu_temp_list
    global time_list
    
    addr_to = "onw4rds@gmail.com"
    addr_from = "onw4rds@gmail.com"
    ## Definimos SMTP del email
    smtp_server = "stmp.gmail.com"
    smtp_user = "onw4rds@gmail.com"
    smtp_pass = "#GOovh47536485q??"
    ## Construimos el email
    message = MIMEMultipart('alternative')
    message['From'] = addr_from
    message['To'] = addr_to  
    message['Subject'] = str(dispositive)+" | "+str(ip)+" | CPU: "+str(cpu_temp_list[-1])+"ºC | GPU: "+str(gpu_temp_list[-1])+"ºC"
    text = """
              Dispositivo:  {0}
              IP:    {1}
              Conexión establecida a las:  {2}
              Temperatura de la CPU: {3} ºC
              Temperatura de la GPU: {4} ºC
                       
              Tiempo de funcionamiento aproximado: {5} minutos""".format(dispositive, ip, 
                                                                         connection_time, 
                                                                         cpu_temp_list[-1], 
                                                                         gpu_temp_list[-1],
                                                                         time_list[-1])
    part1 = MIMEText(text, 'plain')
    message.attach(part1)
    
    
    
    fp = open(str(name_file), 'rb') # se ve la dirección desde index
    attached = MIMEBase('multipart', 'encrypted')
    attached.set_payload(fp.read())
    fp.close()
    # Encriptamos archivo.
    encoders.encode_base64( attached )
    attached.add_header('Content-Disposition', 'attachment', filename = name_file)
    message.attach( attached )
    ## Script para el envío del correo electrónico a la dirección indicada
    mailServer = smtplib.SMTP('smtp.gmail.com', 587)
    mailServer.ehlo()
    mailServer.starttls()
    mailServer.ehlo()
    mailServer.login(smtp_user, smtp_pass)
    mailServer.sendmail(addr_from, addr_to, message.as_string())
    mailServer.quit()

#################################################################################################### 100
    
while(True):
    try:
        while(True):
            #   
            time_list.append(elapsed_time)
            cpu_temp_list.append( get_cpu_temp() )
            gpu_temp_list.append( get_gpu_temp() )
            make_graph(time_list, cpu_temp_list, gpu_temp_list)
    
            send_data("cronData.jpg", connection_time, dispositive, ip)
    
            time.sleep(60)
            elapsed_time += 1
    except:
        pass
    
#################################################################################################### 100

## Conocer nombre del dispositivo y dirección IP de conexión

In [15]:
import socket
import subprocess

dispositivo = socket.gethostname()
ip = subprocess.getoutput('hostname -I')

print(dispositivo)
print(ip)

WD-ZERO
192.168.1.107 


## Conocer tiempo de funcionamiento

In [ ]:
import datetime
import time

initial_time = datetime.datetime.now()

while(True):
    current_time = datetime.datetime.now()
    elapsed_time = current_time - initial_time
    elapsed_time = int(elapsed_time.seconds/60)
    print(elapsed_time)
    time.sleep(10)

0
0
0
0
0
0
1
1
1
1
1
1
2
2
2
2
2
2
3
3
3
3
3
3
4
4
4
4
4
4
5
5
5
5
5
5
6
6
6
6
6
6
7
7
7
7
7
7
8
8
8
8
8
8
9
9
9
9
9
9
10
10
10
10
10
10
11
11
11
11
11
11
12
12
12
12
12
12
13
13
13
13
13
13
14
14
14
14
14
14
15
15
15
15


## Librería wifi para Python
Más información en: https://wifi.readthedocs.io/en/latest/index.html

In [26]:
from wifi import Cell
for cell in Cell.all('wlan0'):
    print("SSID: " + cell.ssid)
    print(cell.signal)
    print(cell.quality)
    print(cell.frequency)
    print(cell.bitrates)
    print(cell.encrypted)
    print(cell.channel)
    print(cell.address)
    print(cell.mode)

SSID: TP-LINK_DCE6
-69
41/70
2.442 GHz
['1 Mb/s', '2 Mb/s', '5.5 Mb/s', '11 Mb/s', '6 Mb/s', '9 Mb/s', '12 Mb/s', '18 Mb/s', '24 Mb/s', '36 Mb/s', '48 Mb/s', '54 Mb/s']
True
7
EC:08:6B:95:13:3D
Master
SSID: vodafone1080
-69
41/70
2.412 GHz
['1 Mb/s', '2 Mb/s', '5.5 Mb/s', '11 Mb/s', '18 Mb/s', '24 Mb/s', '36 Mb/s', '54 Mb/s', '6 Mb/s', '9 Mb/s', '12 Mb/s', '48 Mb/s']
True
1
78:81:02:F1:10:81
Master
SSID: winet fibra optica
-78
32/70
2.457 GHz
['1 Mb/s', '2 Mb/s', '5.5 Mb/s', '11 Mb/s', '6 Mb/s', '9 Mb/s', '12 Mb/s', '18 Mb/s', '24 Mb/s', '36 Mb/s', '48 Mb/s', '54 Mb/s']
True
10
18:D6:C7:44:C9:A2
Master
SSID: vodafoneD88A
-88
22/70
2.412 GHz
['1 Mb/s', '2 Mb/s', '5.5 Mb/s', '11 Mb/s', '18 Mb/s', '24 Mb/s', '36 Mb/s', '54 Mb/s', '6 Mb/s', '9 Mb/s', '12 Mb/s', '48 Mb/s']
True
1
78:94:B4:10:D8:8B
Master
SSID: TP-LINK_DCE6
-84
26/70
2.442 GHz
['1 Mb/s', '2 Mb/s', '5.5 Mb/s', '11 Mb/s', '6 Mb/s', '9 Mb/s', '12 Mb/s', '18 Mb/s', '24 Mb/s', '36 Mb/s', '48 Mb/s', '54 Mb/s']
True
7
18:D6:C7:44:D

## Conocer la temperatura de la CPU

In [6]:
import os

tempFile = open( "/sys/class/thermal/thermal_zone0/temp" )
cpu_temp = tempFile.read()
tempFile.close()
cpu_temp = float(cpu_temp)/1000
print(str(cpu_temp)+"ºC")

31.096ºC


## Conocer la temperatura de la GPU

In [14]:
import subprocess

gpu_temp = subprocess.getoutput( "/opt/vc/bin/vcgencmd measure_temp" ).replace( 'temp=', '' ).replace( 'C', '' )
gpu_temp = float(gpu_temp[:-1])
print(str(gpu_temp)+"ºC")
    #Mostrar temperatura en grados Fahrenheit
    # return float(1.8* gpu_temp)+32

33.2ºC
